In [18]:
from meb.utils import utils
from meb.datasets import datasets
from meb.models import models

import os
from tqdm import tqdm
from typing import Callable, List, Tuple, Union
from functools import partial

import numpy as np
from numba import jit
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.svm import SVC
from sklearn.metrics import f1_score, confusion_matrix
from skimage.transform import resize
import cv2
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
import torch
import torch.nn as nn
import torch.optim as optim
from torchvision import transforms
import timm



pd.set_option("display.max_columns", 50)
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


Code adapted from https://github.com/xiaobaishu0097/MEGC2019

In [2]:
c = datasets.MEGC(cropped=False, color=True)
df = c.data_frame
data = c.data

In [3]:
import dlib
import cv2
from meb.utils import py_evm

In [4]:
detector = dlib.get_frontal_face_detector()
predictor = dlib.shape_predictor("../data/shape_predictor_68_face_landmarks.dat")

In [5]:
def mner_preprocess(onset, apex):
    onset = (onset * 255.0).astype("uint8")
    apex = (apex * 255.0).astype("uint8")
    onset_det = detector(onset, 1)[0] if detector(onset, 1) else detector(onset, 0)[0]
    apex_dets = detector(apex, 1)
    if len(apex_dets) > 0:
        apex_det = apex_dets[0]
    else:
        apex_det = onset_det
    #apex_det = detector(apex, 1)[0]

    onset_face = dlib.full_object_detections()
    apex_face = dlib.full_object_detections()

    onset_face.append(predictor(onset, onset_det))
    apex_face.append(predictor(apex, apex_det))

    onset_crops = dlib.get_face_chips(onset, onset_face, size=320)
    apex_crops = dlib.get_face_chips(apex, apex_face, size=320)

    #Not used, but are in the original code
    #onset_crop = onset_crops[0][:280, 50:270]
    #apex_crop = apex_crops[0][:280, 50:270]

    onset_g = cv2.cvtColor(onset_crops[0], cv2.COLOR_RGB2GRAY)
    apex_g = cv2.cvtColor(apex_crops[0], cv2.COLOR_RGB2GRAY)

    pic_size = onset_crops[0].shape
    hsv = np.zeros(pic_size)
    hsv[:, :, 1] = cv2.cvtColor(apex_crops[0], cv2.COLOR_RGB2HSV)[:, :, 1]

    flow = cv2.calcOpticalFlowFarneback(onset_g, apex_g, flow=None,
                                        pyr_scale=0.5, levels=1, winsize=15,
                                        iterations=2,
                                        poly_n=5, poly_sigma=1.1, flags=0)

    mag, ang = cv2.cartToPolar(flow[..., 0], flow[..., 1])
    hsv[:, :, 0] = ang * (180 / np.pi / 2)
    hsv[:, :, 2] = cv2.normalize(mag, None, 0, 255, cv2.NORM_MINMAX)
    hsv = np.asarray(hsv, dtype=np.float32)
    # This line is added to avoid the bug
    hsv /= 255.0
    rgb_flow = cv2.cvtColor(hsv, cv2.COLOR_HSV2RGB)
    return rgb_flow

In [6]:
flows = np.zeros((df.shape[0], 3, 320, 320))
for i, video in enumerate(tqdm(data, total=df.shape[0])):
    mm_video = py_evm.magnify(video)
    flow = mner_preprocess(mm_video[0], mm_video[df.loc[i, "apexf"]])
    flows[i] = flow.transpose(2, 0, 1)

100%|██████████| 442/442 [2:44:07<00:00, 22.28s/it]  


In [7]:
device = torch.device("cuda:1")

In [8]:
from sklearn.preprocessing import LabelEncoder

In [9]:
le = LabelEncoder()
labels = le.fit_transform(df["emotion"])
dataset = le.fit_transform(df["dataset"])

In [10]:
from torch.utils.data import Dataset

In [11]:
class MEData(Dataset):
    def __init__(self, frames, labels, transform=None):
        self.frames = frames
        self.labels = labels
        self.transform = transform
        
    def __len__(self):
        return self.frames.shape[0]
    
    def __getitem__(self, idx):
        sample = self.frames[idx]
        if self.transform:
            sample = Image.fromarray((sample.transpose(1, 2, 0) * 255).astype("uint8"))
            sample = self.transform(sample)
        label = self.labels[idx]
        return {"image": sample, "label": label}

In [19]:
from torchvision import models

In [20]:
class Resnet18_pt_mcn_removed(nn.Module):
    def __init__(self):
        super(Resnet18_pt_mcn_removed, self).__init__()
        self.meta = {'mean': [0.485, 0.456, 0.406],
                     'std': [0.229, 0.224, 0.225],
                     'imageSize': [224, 224]}
        self.backbone = models.resnet18(pretrained=True)
        self.backbone = torch.nn.Sequential(*(list(self.backbone.children())[:-2]))
        self.features_8 = nn.AvgPool2d(kernel_size=[7, 7], stride=[1, 1], padding=0, ceil_mode=False, count_include_pad=False)
        self.avgpool = nn.AdaptiveAvgPool2d((1, 1))
        
    def forward(self, x):
        features_7 = self.backbone(x)
        
        top = features_7[:, :, :3]
        bottom = features_7[:, :, 3:]
        
        top = self.avgpool(top)
        bottom = self.avgpool(bottom)
        
        top = top.view(top.size(0), -1)
        bottom = bottom.view(bottom.size(0), -1)
        
        return top, bottom
    
    
class FC_3(nn.Module):
    def __init__(self, num_classes=3):
        super(FC_3, self).__init__()
        self.fc_3 = nn.Sequential(
            nn.Linear(512, 64),
            nn.Tanh(),
            nn.Dropout(0.1)
        )

    def forward(self, x):
        x = self.fc_3(x)

        return x

    
class Classifier(nn.Module):
    def __init__(self, input_classes=3, num_classes=3):
        super(Classifier, self).__init__()
        self.fc = nn.Linear(64 * input_classes, num_classes)

    def forward(self, x):
        x = self.fc(x)

        return x

In [21]:
def Flow_Part_npic(num_pic=2, num_classes=3, **kwargs):

    model = {}

    model['resnet'] = Resnet18_pt_mcn_removed()
    model['fc_top'] = FC_3()
    model['fc_bottom'] = FC_3()
    model['classifier'] = Classifier(input_classes=num_pic, num_classes=num_classes)
    model['classifier_top'] = Classifier(input_classes=1, num_classes=num_classes)
    model['classifier_bottom'] = Classifier(input_classes=1, num_classes=num_classes)

    return model

In [22]:
transform = transforms.Compose([
        transforms.Resize((256, 256)),
        transforms.RandomRotation(10),
        transforms.ColorJitter(brightness=0.2, contrast=0.2, saturation=0.2, hue=0.2),
        transforms.RandomCrop((224, 224), pad_if_needed=True),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.5, 0.5, 0.5],
                             std=[0.5, 0.5, 0.5])
    ])

def weight_init(m):
    classname = m.__class__.__name__
    if classname.find('Linear') != -1:
        nn.init.xavier_normal_(m.weight.data)
        nn.init.constant_(m.bias.data, 0.0)

In [16]:
LEARNING_RATE = 0.001

In [17]:
from PIL import Image

In [49]:
#No early stopping
LOSO(flows, df, epochs=100, lr=0.01, weight_decay=0.000001,
     dropout=0.5, batch_size=32, early_stopping=False)

Train:	Epoch:[0][1/14]   	Acc: 0.406	Label_Loss: 1.4189	Top_Loss: 1.7009	Bottom_Loss: 2.1371	Loss: 5.2569	
Train:	Epoch:[0][8/14]   	Acc: 0.375	Label_Loss: 1.3505	Top_Loss: 1.2114	Bottom_Loss: 1.2450	Loss: 3.8068	
Subject: 006, n=11 | test_f1: 0.2807 |best_f1: 0.2807
Train:	Epoch:[1][1/14]   	Acc: 0.562	Label_Loss: 0.9894	Top_Loss: 0.9396	Bottom_Loss: 1.0860	Loss: 3.0150	
Train:	Epoch:[1][8/14]   	Acc: 0.531	Label_Loss: 0.9697	Top_Loss: 1.0461	Bottom_Loss: 0.9797	Loss: 2.9955	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.45
Train:	Epoch:[2][1/14]   	Acc: 0.594	Label_Loss: 0.9505	Top_Loss: 0.7569	Bottom_Loss: 0.9643	Loss: 2.6717	
Train:	Epoch:[2][8/14]   	Acc: 0.500	Label_Loss: 1.1038	Top_Loss: 0.9681	Bottom_Loss: 1.0106	Loss: 3.0825	
Subject: 006, n=11 | test_f1: 0.42105 |best_f1: 0.45
Train:	Epoch:[3][1/14]   	Acc: 0.469	Label_Loss: 0.9632	Top_Loss: 1.0003	Bottom_Loss: 0.9059	Loss: 2.8694	
Train:	Epoch:[3][8/14]   	Acc: 0.531	Label_Loss: 0.9506	Top_Loss: 0.9213	Bottom_Loss: 1.0243	L

Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.45
Train:	Epoch:[31][1/14]   	Acc: 0.875	Label_Loss: 0.3142	Top_Loss: 0.4742	Bottom_Loss: 0.4209	Loss: 1.2094	
Train:	Epoch:[31][8/14]   	Acc: 0.906	Label_Loss: 0.2948	Top_Loss: 0.5128	Bottom_Loss: 0.4497	Loss: 1.2573	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.45
Train:	Epoch:[32][1/14]   	Acc: 0.938	Label_Loss: 0.3749	Top_Loss: 0.5159	Bottom_Loss: 0.4619	Loss: 1.3527	
Train:	Epoch:[32][8/14]   	Acc: 0.781	Label_Loss: 0.3682	Top_Loss: 0.6612	Bottom_Loss: 0.3221	Loss: 1.3514	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.45
Train:	Epoch:[33][1/14]   	Acc: 0.906	Label_Loss: 0.2172	Top_Loss: 0.4137	Bottom_Loss: 0.3648	Loss: 0.9957	
Train:	Epoch:[33][8/14]   	Acc: 0.938	Label_Loss: 0.1868	Top_Loss: 0.2813	Bottom_Loss: 0.3340	Loss: 0.8021	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.45
Train:	Epoch:[34][1/14]   	Acc: 0.875	Label_Loss: 0.2297	Top_Loss: 0.3594	Bottom_Loss: 0.3854	Loss: 0.9745	
Train:	Epoch:[34][8/14]   	Acc: 0.906	Label_

Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.45
Train:	Epoch:[62][1/14]   	Acc: 1.000	Label_Loss: 0.0286	Top_Loss: 0.0804	Bottom_Loss: 0.0724	Loss: 0.1814	
Train:	Epoch:[62][8/14]   	Acc: 1.000	Label_Loss: 0.0753	Top_Loss: 0.1107	Bottom_Loss: 0.2442	Loss: 0.4301	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.45
Train:	Epoch:[63][1/14]   	Acc: 1.000	Label_Loss: 0.0139	Top_Loss: 0.0906	Bottom_Loss: 0.0398	Loss: 0.1443	
Train:	Epoch:[63][8/14]   	Acc: 1.000	Label_Loss: 0.0231	Top_Loss: 0.0934	Bottom_Loss: 0.0666	Loss: 0.1831	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.45
Train:	Epoch:[64][1/14]   	Acc: 0.969	Label_Loss: 0.0641	Top_Loss: 0.1890	Bottom_Loss: 0.0773	Loss: 0.3304	
Train:	Epoch:[64][8/14]   	Acc: 1.000	Label_Loss: 0.0224	Top_Loss: 0.1300	Bottom_Loss: 0.0979	Loss: 0.2504	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.45
Train:	Epoch:[65][1/14]   	Acc: 1.000	Label_Loss: 0.0228	Top_Loss: 0.0607	Bottom_Loss: 0.1226	Loss: 0.2060	
Train:	Epoch:[65][8/14]   	Acc: 1.000	Label_

Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[93][1/14]   	Acc: 1.000	Label_Loss: 0.0103	Top_Loss: 0.0352	Bottom_Loss: 0.0205	Loss: 0.0659	
Train:	Epoch:[93][8/14]   	Acc: 1.000	Label_Loss: 0.0087	Top_Loss: 0.0778	Bottom_Loss: 0.0220	Loss: 0.1085	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[94][1/14]   	Acc: 1.000	Label_Loss: 0.0145	Top_Loss: 0.0461	Bottom_Loss: 0.0275	Loss: 0.0881	
Train:	Epoch:[94][8/14]   	Acc: 1.000	Label_Loss: 0.0099	Top_Loss: 0.0957	Bottom_Loss: 0.0138	Loss: 0.1193	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[95][1/14]   	Acc: 1.000	Label_Loss: 0.0291	Top_Loss: 0.0573	Bottom_Loss: 0.0626	Loss: 0.1491	
Train:	Epoch:[95][8/14]   	Acc: 1.000	Label_Loss: 0.0088	Top_Loss: 0.0755	Bottom_Loss: 0.0157	Loss: 0.1000	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[96][1/14]   	Acc: 1.000	Label_Loss: 0.0144	Top_Loss: 0.0514	Bottom_Loss: 0.0299	Loss: 0.0956	
Train:	Epoch:[96][8/14]   	Acc: 

Train:	Epoch:[23][1/14]   	Acc: 0.906	Label_Loss: 0.2612	Top_Loss: 0.3649	Bottom_Loss: 0.3651	Loss: 0.9912	
Train:	Epoch:[23][8/14]   	Acc: 0.969	Label_Loss: 0.2102	Top_Loss: 0.4488	Bottom_Loss: 0.3814	Loss: 1.0404	
Subject: 007, n=08 | test_f1: 0.074074 |best_f1: 0.19444
Train:	Epoch:[24][1/14]   	Acc: 0.906	Label_Loss: 0.3879	Top_Loss: 0.5432	Bottom_Loss: 0.5355	Loss: 1.4666	
Train:	Epoch:[24][8/14]   	Acc: 0.812	Label_Loss: 0.4731	Top_Loss: 0.4698	Bottom_Loss: 0.5253	Loss: 1.4682	
Subject: 007, n=08 | test_f1: 0.074074 |best_f1: 0.19444
Train:	Epoch:[25][1/14]   	Acc: 0.938	Label_Loss: 0.2312	Top_Loss: 0.4111	Bottom_Loss: 0.4266	Loss: 1.0689	
Train:	Epoch:[25][8/14]   	Acc: 0.656	Label_Loss: 0.6408	Top_Loss: 0.8175	Bottom_Loss: 0.6220	Loss: 2.0804	
Subject: 007, n=08 | test_f1: 0.19444 |best_f1: 0.19444
Train:	Epoch:[26][1/14]   	Acc: 0.938	Label_Loss: 0.2052	Top_Loss: 0.3963	Bottom_Loss: 0.3731	Loss: 0.9746	
Train:	Epoch:[26][8/14]   	Acc: 0.969	Label_Loss: 0.1662	Top_Loss: 0.3025	

...

Train:	Epoch:[62][8/14]   	Acc: 1.000	Label_Loss: 0.0297	Top_Loss: 0.0873	Bottom_Loss: 0.0832	Loss: 0.2002	
Subject: s8, n=13 | test_f1: 0.22727 |best_f1: 0.62857
Train:	Epoch:[63][1/14]   	Acc: 1.000	Label_Loss: 0.0548	Top_Loss: 0.1291	Bottom_Loss: 0.1324	Loss: 0.3162	
Train:	Epoch:[63][8/14]   	Acc: 0.969	Label_Loss: 0.0609	Top_Loss: 0.0962	Bottom_Loss: 0.1566	Loss: 0.3137	
Subject: s8, n=13 | test_f1: 0.37037 |best_f1: 0.62857
Train:	Epoch:[64][1/14]   	Acc: 0.969	Label_Loss: 0.0561	Top_Loss: 0.1582	Bottom_Loss: 0.0753	Loss: 0.2896	
Train:	Epoch:[64][8/14]   	Acc: 0.938	Label_Loss: 0.0933	Top_Loss: 0.1996	Bottom_Loss: 0.0980	Loss: 0.3909	
Subject: s8, n=13 | test_f1: 0.43333 |best_f1: 0.62857
Train:	Epoch:[65][1/14]   	Acc: 1.000	Label_Loss: 0.0298	Top_Loss: 0.1315	Bottom_Loss: 0.0839	Loss: 0.2452	
Train:	Epoch:[65][8/14]   	Acc: 1.000	Label_Loss: 0.0315	Top_Loss: 0.0934	Bottom_Loss: 0.0763	Loss: 0.2012	
Subject: s8, n=13 | test_f1: 0.375 |best_f1: 0.62857
Train:	Epoch:[66][1/14]   

Subject: s8, n=13 | test_f1: 0.12727 |best_f1: 0.62857
Train:	Epoch:[93][1/14]   	Acc: 0.969	Label_Loss: 0.0408	Top_Loss: 0.0757	Bottom_Loss: 0.0426	Loss: 0.1591	
Train:	Epoch:[93][8/14]   	Acc: 1.000	Label_Loss: 0.0064	Top_Loss: 0.0343	Bottom_Loss: 0.0181	Loss: 0.0587	
Subject: s8, n=13 | test_f1: 0.25 |best_f1: 0.62857
Train:	Epoch:[94][1/14]   	Acc: 1.000	Label_Loss: 0.0084	Top_Loss: 0.0298	Bottom_Loss: 0.0147	Loss: 0.0529	
Train:	Epoch:[94][8/14]   	Acc: 1.000	Label_Loss: 0.0039	Top_Loss: 0.0108	Bottom_Loss: 0.0323	Loss: 0.0470	
Subject: s8, n=13 | test_f1: 0.4881 |best_f1: 0.62857
Train:	Epoch:[95][1/14]   	Acc: 1.000	Label_Loss: 0.0178	Top_Loss: 0.0377	Bottom_Loss: 0.0325	Loss: 0.0881	
Train:	Epoch:[95][8/14]   	Acc: 1.000	Label_Loss: 0.0114	Top_Loss: 0.0212	Bottom_Loss: 0.0376	Loss: 0.0702	
Subject: s8, n=13 | test_f1: 0.37179 |best_f1: 0.62857
Train:	Epoch:[96][1/14]   	Acc: 1.000	Label_Loss: 0.0251	Top_Loss: 0.0342	Bottom_Loss: 0.0728	Loss: 0.1322	
Train:	Epoch:[96][8/14]   	A

Train:	Epoch:[23][8/14]   	Acc: 0.906	Label_Loss: 0.4095	Top_Loss: 0.5749	Bottom_Loss: 0.5400	Loss: 1.5244	
Subject: s9, n=04 | test_f1: 0.38889 |best_f1: 0.73333
Train:	Epoch:[24][1/14]   	Acc: 0.906	Label_Loss: 0.3029	Top_Loss: 0.4199	Bottom_Loss: 0.4956	Loss: 1.2184	
Train:	Epoch:[24][8/14]   	Acc: 0.844	Label_Loss: 0.3907	Top_Loss: 0.5965	Bottom_Loss: 0.3743	Loss: 1.3615	
Subject: s9, n=04 | test_f1: 0.22222 |best_f1: 0.73333
Train:	Epoch:[25][1/14]   	Acc: 0.906	Label_Loss: 0.2589	Top_Loss: 0.3547	Bottom_Loss: 0.3312	Loss: 0.9448	
Train:	Epoch:[25][8/14]   	Acc: 0.844	Label_Loss: 0.4457	Top_Loss: 0.4175	Bottom_Loss: 0.5706	Loss: 1.4338	
Subject: s9, n=04 | test_f1: 0.16667 |best_f1: 0.73333
Train:	Epoch:[26][1/14]   	Acc: 0.875	Label_Loss: 0.3303	Top_Loss: 0.5888	Bottom_Loss: 0.3723	Loss: 1.2914	
Train:	Epoch:[26][8/14]   	Acc: 0.969	Label_Loss: 0.2600	Top_Loss: 0.3661	Bottom_Loss: 0.4885	Loss: 1.1146	
Subject: s9, n=04 | test_f1: 0.22222 |best_f1: 0.73333
Train:	Epoch:[27][1/14] 

Train:	Epoch:[54][1/14]   	Acc: 1.000	Label_Loss: 0.0476	Top_Loss: 0.1433	Bottom_Loss: 0.0983	Loss: 0.2892	
Train:	Epoch:[54][8/14]   	Acc: 1.000	Label_Loss: 0.0558	Top_Loss: 0.1364	Bottom_Loss: 0.1639	Loss: 0.3560	
Subject: s9, n=04 | test_f1: 0.16667 |best_f1: 0.73333
Train:	Epoch:[55][1/14]   	Acc: 1.000	Label_Loss: 0.0146	Top_Loss: 0.0891	Bottom_Loss: 0.0681	Loss: 0.1718	
Train:	Epoch:[55][8/14]   	Acc: 1.000	Label_Loss: 0.0373	Top_Loss: 0.1879	Bottom_Loss: 0.1064	Loss: 0.3316	
Subject: s9, n=04 | test_f1: 0.0 |best_f1: 0.73333
Train:	Epoch:[56][1/14]   	Acc: 1.000	Label_Loss: 0.0617	Top_Loss: 0.1730	Bottom_Loss: 0.1401	Loss: 0.3748	
Train:	Epoch:[56][8/14]   	Acc: 1.000	Label_Loss: 0.0368	Top_Loss: 0.0855	Bottom_Loss: 0.1451	Loss: 0.2674	
Subject: s9, n=04 | test_f1: 0.22222 |best_f1: 0.73333
Train:	Epoch:[57][1/14]   	Acc: 0.969	Label_Loss: 0.0730	Top_Loss: 0.0973	Bottom_Loss: 0.1132	Loss: 0.2835	
Train:	Epoch:[57][8/14]   	Acc: 1.000	Label_Loss: 0.0829	Top_Loss: 0.2136	Bottom_Lo

Subject: s9, n=04 | test_f1: 0.38889 |best_f1: 1.0
Train:	Epoch:[85][1/14]   	Acc: 1.000	Label_Loss: 0.0200	Top_Loss: 0.0693	Bottom_Loss: 0.0556	Loss: 0.1448	
Train:	Epoch:[85][8/14]   	Acc: 1.000	Label_Loss: 0.0253	Top_Loss: 0.0465	Bottom_Loss: 0.0593	Loss: 0.1311	
Subject: s9, n=04 | test_f1: 0.73333 |best_f1: 1.0
Train:	Epoch:[86][1/14]   	Acc: 1.000	Label_Loss: 0.0140	Top_Loss: 0.0382	Bottom_Loss: 0.0253	Loss: 0.0775	
Train:	Epoch:[86][8/14]   	Acc: 1.000	Label_Loss: 0.0092	Top_Loss: 0.0584	Bottom_Loss: 0.0291	Loss: 0.0968	
Subject: s9, n=04 | test_f1: 0.5 |best_f1: 1.0
Train:	Epoch:[87][1/14]   	Acc: 1.000	Label_Loss: 0.0104	Top_Loss: 0.0830	Bottom_Loss: 0.0154	Loss: 0.1087	
Train:	Epoch:[87][8/14]   	Acc: 1.000	Label_Loss: 0.0168	Top_Loss: 0.0741	Bottom_Loss: 0.0700	Loss: 0.1609	
Subject: s9, n=04 | test_f1: 0.5 |best_f1: 1.0
Train:	Epoch:[88][1/14]   	Acc: 0.969	Label_Loss: 0.0422	Top_Loss: 0.0688	Bottom_Loss: 0.0642	Loss: 0.1752	
Train:	Epoch:[88][8/14]   	Acc: 1.000	Label_Loss

In [53]:
#Test early stopping
LOSO(flows, df, epochs=100, lr=0.01, weight_decay=0.000001,
     dropout=0.5, batch_size=32, early_stopping=True)

Train:	Epoch:[0][1/14]   	Acc: 0.188	Label_Loss: 1.6815	Top_Loss: 1.0724	Bottom_Loss: 1.5611	Loss: 4.3149	
Train:	Epoch:[0][8/14]   	Acc: 0.531	Label_Loss: 0.9904	Top_Loss: 1.0640	Bottom_Loss: 1.2593	Loss: 3.3137	
Subject: 006, n=11 | test_f1: 0.80702 |best_f1: 0.80702
Train:	Epoch:[1][1/14]   	Acc: 0.375	Label_Loss: 1.3380	Top_Loss: 1.4450	Bottom_Loss: 1.4637	Loss: 4.2467	
Train:	Epoch:[1][8/14]   	Acc: 0.562	Label_Loss: 0.8807	Top_Loss: 0.8503	Bottom_Loss: 0.9432	Loss: 2.6743	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[2][1/14]   	Acc: 0.531	Label_Loss: 0.9749	Top_Loss: 1.1406	Bottom_Loss: 0.9712	Loss: 3.0867	
Train:	Epoch:[2][8/14]   	Acc: 0.656	Label_Loss: 0.8348	Top_Loss: 0.9363	Bottom_Loss: 0.9841	Loss: 2.7552	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[3][1/14]   	Acc: 0.500	Label_Loss: 0.9885	Top_Loss: 0.8798	Bottom_Loss: 0.9335	Loss: 2.8017	
Train:	Epoch:[3][8/14]   	Acc: 0.469	Label_Loss: 1.0986	Top_Loss: 1.0136	Bottom_Loss: 0.9

Train:	Epoch:[30][8/14]   	Acc: 0.938	Label_Loss: 0.2615	Top_Loss: 0.4562	Bottom_Loss: 0.5555	Loss: 1.2731	
Subject: 006, n=11 | test_f1: 0.80702 |best_f1: 0.80702
Train:	Epoch:[31][1/14]   	Acc: 0.906	Label_Loss: 0.2843	Top_Loss: 0.4315	Bottom_Loss: 0.3581	Loss: 1.0739	
Train:	Epoch:[31][8/14]   	Acc: 0.906	Label_Loss: 0.2859	Top_Loss: 0.3443	Bottom_Loss: 0.4228	Loss: 1.0530	
Subject: 006, n=11 | test_f1: 0.31579 |best_f1: 0.80702
Train:	Epoch:[32][1/14]   	Acc: 0.906	Label_Loss: 0.2115	Top_Loss: 0.4183	Bottom_Loss: 0.3953	Loss: 1.0251	
Train:	Epoch:[32][8/14]   	Acc: 0.875	Label_Loss: 0.2496	Top_Loss: 0.4961	Bottom_Loss: 0.4835	Loss: 1.2291	
Subject: 006, n=11 | test_f1: 0.38889 |best_f1: 0.80702
Train:	Epoch:[33][1/14]   	Acc: 0.938	Label_Loss: 0.2527	Top_Loss: 0.3438	Bottom_Loss: 0.3885	Loss: 0.9849	
Train:	Epoch:[33][8/14]   	Acc: 0.938	Label_Loss: 0.2220	Top_Loss: 0.3602	Bottom_Loss: 0.2859	Loss: 0.8682	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[34][1/14]

Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[61][1/14]   	Acc: 1.000	Label_Loss: 0.0226	Top_Loss: 0.1051	Bottom_Loss: 0.0702	Loss: 0.1979	
Train:	Epoch:[61][8/14]   	Acc: 1.000	Label_Loss: 0.0426	Top_Loss: 0.0794	Bottom_Loss: 0.1612	Loss: 0.2832	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[62][1/14]   	Acc: 1.000	Label_Loss: 0.0420	Top_Loss: 0.0921	Bottom_Loss: 0.1396	Loss: 0.2736	
Train:	Epoch:[62][8/14]   	Acc: 0.938	Label_Loss: 0.1415	Top_Loss: 0.2519	Bottom_Loss: 0.1893	Loss: 0.5827	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[63][1/14]   	Acc: 1.000	Label_Loss: 0.0335	Top_Loss: 0.0804	Bottom_Loss: 0.0853	Loss: 0.1992	
Train:	Epoch:[63][8/14]   	Acc: 0.969	Label_Loss: 0.0785	Top_Loss: 0.2187	Bottom_Loss: 0.1484	Loss: 0.4457	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[64][1/14]   	Acc: 0.938	Label_Loss: 0.1482	Top_Loss: 0.2514	Bottom_Loss: 0.1882	Loss: 0.5878	
Train:	Epoch:[64][8/14]   	Acc: 

Train:	Epoch:[91][8/14]   	Acc: 1.000	Label_Loss: 0.0073	Top_Loss: 0.0173	Bottom_Loss: 0.0491	Loss: 0.0738	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[92][1/14]   	Acc: 1.000	Label_Loss: 0.0099	Top_Loss: 0.0269	Bottom_Loss: 0.0366	Loss: 0.0735	
Train:	Epoch:[92][8/14]   	Acc: 1.000	Label_Loss: 0.0234	Top_Loss: 0.0969	Bottom_Loss: 0.0241	Loss: 0.1444	
Subject: 006, n=11 | test_f1: 0.80702 |best_f1: 0.80702
Train:	Epoch:[93][1/14]   	Acc: 1.000	Label_Loss: 0.0090	Top_Loss: 0.0430	Bottom_Loss: 0.0173	Loss: 0.0693	
Train:	Epoch:[93][8/14]   	Acc: 1.000	Label_Loss: 0.0050	Top_Loss: 0.0378	Bottom_Loss: 0.0126	Loss: 0.0554	
Subject: 006, n=11 | test_f1: 0.45 |best_f1: 0.80702
Train:	Epoch:[94][1/14]   	Acc: 0.969	Label_Loss: 0.1026	Top_Loss: 0.1183	Bottom_Loss: 0.0554	Loss: 0.2763	
Train:	Epoch:[94][8/14]   	Acc: 1.000	Label_Loss: 0.0152	Top_Loss: 0.0229	Bottom_Loss: 0.1001	Loss: 0.1383	
Subject: 006, n=11 | test_f1: 0.42105 |best_f1: 0.80702
Train:	Epoch:[95][1/14]   

Subject: 007, n=08 | test_f1: 0.19444 |best_f1: 0.42857
Train:	Epoch:[22][1/14]   	Acc: 0.969	Label_Loss: 0.2272	Top_Loss: 0.3689	Bottom_Loss: 0.4030	Loss: 0.9992	
Train:	Epoch:[22][8/14]   	Acc: 0.812	Label_Loss: 0.4330	Top_Loss: 0.3630	Bottom_Loss: 0.5463	Loss: 1.3424	
Subject: 007, n=08 | test_f1: 0.0 |best_f1: 0.42857
Train:	Epoch:[23][1/14]   	Acc: 0.969	Label_Loss: 0.2295	Top_Loss: 0.3919	Bottom_Loss: 0.4213	Loss: 1.0427	
Train:	Epoch:[23][8/14]   	Acc: 0.844	Label_Loss: 0.3606	Top_Loss: 0.5433	Bottom_Loss: 0.4690	Loss: 1.3729	
Subject: 007, n=08 | test_f1: 0.074074 |best_f1: 0.42857
Train:	Epoch:[24][1/14]   	Acc: 0.906	Label_Loss: 0.3173	Top_Loss: 0.4690	Bottom_Loss: 0.4207	Loss: 1.2070	
Train:	Epoch:[24][8/14]   	Acc: 0.906	Label_Loss: 0.2935	Top_Loss: 0.3851	Bottom_Loss: 0.4081	Loss: 1.0867	
Subject: 007, n=08 | test_f1: 0.083333 |best_f1: 0.42857
Train:	Epoch:[25][1/14]   	Acc: 0.938	Label_Loss: 0.2112	Top_Loss: 0.3403	Bottom_Loss: 0.4196	Loss: 0.9711	
Train:	Epoch:[25][8/14

...

Train:	Epoch:[63][8/14]   	Acc: 1.000	Label_Loss: 0.0427	Top_Loss: 0.0753	Bottom_Loss: 0.1167	Loss: 0.2347	
Subject: s8, n=13 | test_f1: 0.27179 |best_f1: 0.76364
Train:	Epoch:[64][1/14]   	Acc: 1.000	Label_Loss: 0.0314	Top_Loss: 0.0595	Bottom_Loss: 0.0960	Loss: 0.1870	
Train:	Epoch:[64][8/14]   	Acc: 1.000	Label_Loss: 0.0672	Top_Loss: 0.2362	Bottom_Loss: 0.1166	Loss: 0.4199	
Subject: s8, n=13 | test_f1: 0.32121 |best_f1: 0.76364
Train:	Epoch:[65][1/14]   	Acc: 1.000	Label_Loss: 0.0340	Top_Loss: 0.1208	Bottom_Loss: 0.0889	Loss: 0.2438	
Train:	Epoch:[65][8/14]   	Acc: 1.000	Label_Loss: 0.0632	Top_Loss: 0.1541	Bottom_Loss: 0.1158	Loss: 0.3332	
Subject: s8, n=13 | test_f1: 0.30357 |best_f1: 0.76364
Train:	Epoch:[66][1/14]   	Acc: 1.000	Label_Loss: 0.0338	Top_Loss: 0.0960	Bottom_Loss: 0.1179	Loss: 0.2477	
Train:	Epoch:[66][8/14]   	Acc: 1.000	Label_Loss: 0.0335	Top_Loss: 0.1132	Bottom_Loss: 0.1021	Loss: 0.2489	
Subject: s8, n=13 | test_f1: 0.32381 |best_f1: 0.76364
Train:	Epoch:[67][1/14] 

Subject: s8, n=13 | test_f1: 0.30199 |best_f1: 0.76364
Train:	Epoch:[94][1/14]   	Acc: 1.000	Label_Loss: 0.0157	Top_Loss: 0.1069	Bottom_Loss: 0.0221	Loss: 0.1447	
Train:	Epoch:[94][8/14]   	Acc: 1.000	Label_Loss: 0.0193	Top_Loss: 0.0362	Bottom_Loss: 0.0362	Loss: 0.0917	
Subject: s8, n=13 | test_f1: 0.28571 |best_f1: 0.76364
Train:	Epoch:[95][1/14]   	Acc: 1.000	Label_Loss: 0.0065	Top_Loss: 0.0249	Bottom_Loss: 0.0327	Loss: 0.0641	
Train:	Epoch:[95][8/14]   	Acc: 1.000	Label_Loss: 0.0046	Top_Loss: 0.0546	Bottom_Loss: 0.0238	Loss: 0.0830	
Subject: s8, n=13 | test_f1: 0.30556 |best_f1: 0.76364
Train:	Epoch:[96][1/14]   	Acc: 1.000	Label_Loss: 0.0085	Top_Loss: 0.0180	Bottom_Loss: 0.0288	Loss: 0.0553	
Train:	Epoch:[96][8/14]   	Acc: 1.000	Label_Loss: 0.0052	Top_Loss: 0.0145	Bottom_Loss: 0.0489	Loss: 0.0686	
Subject: s8, n=13 | test_f1: 0.27381 |best_f1: 0.76364
Train:	Epoch:[97][1/14]   	Acc: 1.000	Label_Loss: 0.0076	Top_Loss: 0.0228	Bottom_Loss: 0.0196	Loss: 0.0500	
Train:	Epoch:[97][8/14] 

Train:	Epoch:[24][8/14]   	Acc: 0.938	Label_Loss: 0.2427	Top_Loss: 0.4585	Bottom_Loss: 0.4067	Loss: 1.1080	
Subject: s9, n=04 | test_f1: 0.0 |best_f1: 0.38889
Train:	Epoch:[25][1/14]   	Acc: 0.938	Label_Loss: 0.2223	Top_Loss: 0.3713	Bottom_Loss: 0.4146	Loss: 1.0082	
Train:	Epoch:[25][8/14]   	Acc: 0.844	Label_Loss: 0.2997	Top_Loss: 0.5286	Bottom_Loss: 0.4096	Loss: 1.2379	
Subject: s9, n=04 | test_f1: 0.5 |best_f1: 0.5
Train:	Epoch:[26][1/14]   	Acc: 0.750	Label_Loss: 0.5163	Top_Loss: 0.6774	Bottom_Loss: 0.6136	Loss: 1.8072	
Train:	Epoch:[26][8/14]   	Acc: 0.844	Label_Loss: 0.3487	Top_Loss: 0.5734	Bottom_Loss: 0.3992	Loss: 1.3213	
Subject: s9, n=04 | test_f1: 0.5 |best_f1: 0.5
Train:	Epoch:[27][1/14]   	Acc: 0.938	Label_Loss: 0.2550	Top_Loss: 0.3809	Bottom_Loss: 0.4217	Loss: 1.0576	
Train:	Epoch:[27][8/14]   	Acc: 0.844	Label_Loss: 0.3598	Top_Loss: 0.4842	Bottom_Loss: 0.4383	Loss: 1.2823	
Subject: s9, n=04 | test_f1: 0.0 |best_f1: 0.5
Train:	Epoch:[28][1/14]   	Acc: 0.844	Label_Loss: 0.

Train:	Epoch:[55][8/14]   	Acc: 0.969	Label_Loss: 0.1199	Top_Loss: 0.3294	Bottom_Loss: 0.0921	Loss: 0.5414	
Subject: s9, n=04 | test_f1: 0.16667 |best_f1: 0.73333
Train:	Epoch:[56][1/14]   	Acc: 1.000	Label_Loss: 0.0440	Top_Loss: 0.0629	Bottom_Loss: 0.1704	Loss: 0.2773	
Train:	Epoch:[56][8/14]   	Acc: 1.000	Label_Loss: 0.0523	Top_Loss: 0.1674	Bottom_Loss: 0.1487	Loss: 0.3684	
Subject: s9, n=04 | test_f1: 0.5 |best_f1: 0.73333
Train:	Epoch:[57][1/14]   	Acc: 0.969	Label_Loss: 0.0780	Top_Loss: 0.1119	Bottom_Loss: 0.1914	Loss: 0.3813	
Train:	Epoch:[57][8/14]   	Acc: 0.969	Label_Loss: 0.1506	Top_Loss: 0.1664	Bottom_Loss: 0.2060	Loss: 0.5230	
Subject: s9, n=04 | test_f1: 0.16667 |best_f1: 0.73333
Train:	Epoch:[58][1/14]   	Acc: 1.000	Label_Loss: 0.0629	Top_Loss: 0.1319	Bottom_Loss: 0.1305	Loss: 0.3254	
Train:	Epoch:[58][8/14]   	Acc: 1.000	Label_Loss: 0.0161	Top_Loss: 0.1315	Bottom_Loss: 0.0340	Loss: 0.1816	
Subject: s9, n=04 | test_f1: 0.33333 |best_f1: 0.73333
Train:	Epoch:[59][1/14]   	A

Train:	Epoch:[86][1/14]   	Acc: 1.000	Label_Loss: 0.0189	Top_Loss: 0.0760	Bottom_Loss: 0.0457	Loss: 0.1405	
Train:	Epoch:[86][8/14]   	Acc: 1.000	Label_Loss: 0.0212	Top_Loss: 0.0518	Bottom_Loss: 0.0383	Loss: 0.1113	
Subject: s9, n=04 | test_f1: 0.26667 |best_f1: 0.73333
Train:	Epoch:[87][1/14]   	Acc: 1.000	Label_Loss: 0.0110	Top_Loss: 0.0486	Bottom_Loss: 0.0589	Loss: 0.1185	
Train:	Epoch:[87][8/14]   	Acc: 1.000	Label_Loss: 0.0140	Top_Loss: 0.0455	Bottom_Loss: 0.0173	Loss: 0.0768	
Subject: s9, n=04 | test_f1: 0.16667 |best_f1: 0.73333
Train:	Epoch:[88][1/14]   	Acc: 0.969	Label_Loss: 0.0517	Top_Loss: 0.1296	Bottom_Loss: 0.0952	Loss: 0.2766	
Train:	Epoch:[88][8/14]   	Acc: 1.000	Label_Loss: 0.0060	Top_Loss: 0.0566	Bottom_Loss: 0.0162	Loss: 0.0788	
Subject: s9, n=04 | test_f1: 0.16667 |best_f1: 0.73333
Train:	Epoch:[89][1/14]   	Acc: 1.000	Label_Loss: 0.0052	Top_Loss: 0.0312	Bottom_Loss: 0.0221	Loss: 0.0585	
Train:	Epoch:[89][8/14]   	Acc: 1.000	Label_Loss: 0.0111	Top_Loss: 0.0246	Botto

In [21]:
#Validation early stopping
LOSO(flows, df, epochs=100, lr=0.01, weight_decay=0.000001,
     dropout=0.5, batch_size=32, early_stopping=True)

Train:	Epoch:[0][1/11]   	Acc: 0.312	Label_Loss: 1.9880	Top_Loss: 1.2481	Bottom_Loss: 1.7352	Loss: 4.9714	
Train:	Epoch:[0][8/11]   	Acc: 0.375	Label_Loss: 1.3391	Top_Loss: 1.1974	Bottom_Loss: 1.1838	Loss: 3.7203	
Subject: 006, n=11 | test_f1: 0.45 | val_f1: 0.33311 |best_f1: 0.33311
Train:	Epoch:[1][1/11]   	Acc: 0.312	Label_Loss: 1.0812	Top_Loss: 0.7590	Bottom_Loss: 0.9970	Loss: 2.8371	
Train:	Epoch:[1][8/11]   	Acc: 0.500	Label_Loss: 1.0066	Top_Loss: 1.0067	Bottom_Loss: 0.9230	Loss: 2.9362	
Subject: 006, n=11 | test_f1: 0.45 | val_f1: 0.32565 |best_f1: 0.33311
Train:	Epoch:[2][1/11]   	Acc: 0.500	Label_Loss: 1.0514	Top_Loss: 0.9179	Bottom_Loss: 1.1554	Loss: 3.1248	
Train:	Epoch:[2][8/11]   	Acc: 0.656	Label_Loss: 0.9211	Top_Loss: 0.9350	Bottom_Loss: 0.9484	Loss: 2.8046	
Subject: 006, n=11 | test_f1: 0.45 | val_f1: 0.45351 |best_f1: 0.45351
Train:	Epoch:[3][1/11]   	Acc: 0.750	Label_Loss: 0.7160	Top_Loss: 0.8379	Bottom_Loss: 0.9909	Loss: 2.5449	
Train:	Epoch:[3][8/11]   	Acc: 0.719	L

Subject: 006, n=11 | test_f1: 0.42105 | val_f1: 0.43801 |best_f1: 0.57168
Train:	Epoch:[29][1/11]   	Acc: 0.938	Label_Loss: 0.1733	Top_Loss: 0.2945	Bottom_Loss: 0.3407	Loss: 0.8085	
Train:	Epoch:[29][8/11]   	Acc: 0.906	Label_Loss: 0.3287	Top_Loss: 0.4594	Bottom_Loss: 0.5469	Loss: 1.3350	
Subject: 006, n=11 | test_f1: 0.42105 | val_f1: 0.55037 |best_f1: 0.57168
Train:	Epoch:[30][1/11]   	Acc: 0.875	Label_Loss: 0.2261	Top_Loss: 0.2883	Bottom_Loss: 0.3503	Loss: 0.8646	
Train:	Epoch:[30][8/11]   	Acc: 0.906	Label_Loss: 0.3171	Top_Loss: 0.4566	Bottom_Loss: 0.4401	Loss: 1.2138	
Subject: 006, n=11 | test_f1: 0.42105 | val_f1: 0.55977 |best_f1: 0.57168
Train:	Epoch:[31][1/11]   	Acc: 0.938	Label_Loss: 0.2733	Top_Loss: 0.3647	Bottom_Loss: 0.4973	Loss: 1.1352	
Train:	Epoch:[31][8/11]   	Acc: 1.000	Label_Loss: 0.1205	Top_Loss: 0.3333	Bottom_Loss: 0.2997	Loss: 0.7535	
Subject: 006, n=11 | test_f1: 0.2963 | val_f1: 0.5841 |best_f1: 0.5841
Train:	Epoch:[32][1/11]   	Acc: 0.969	Label_Loss: 0.2368	To

Train:	Epoch:[57][8/11]   	Acc: 0.969	Label_Loss: 0.0829	Top_Loss: 0.1690	Bottom_Loss: 0.1409	Loss: 0.3927	
Subject: 006, n=11 | test_f1: 0.42105 | val_f1: 0.50097 |best_f1: 0.64708
Train:	Epoch:[58][1/11]   	Acc: 0.969	Label_Loss: 0.0961	Top_Loss: 0.1780	Bottom_Loss: 0.1598	Loss: 0.4339	
Train:	Epoch:[58][8/11]   	Acc: 1.000	Label_Loss: 0.0568	Top_Loss: 0.1533	Bottom_Loss: 0.0852	Loss: 0.2953	
Subject: 006, n=11 | test_f1: 0.45 | val_f1: 0.47825 |best_f1: 0.64708
Train:	Epoch:[59][1/11]   	Acc: 0.969	Label_Loss: 0.0720	Top_Loss: 0.0901	Bottom_Loss: 0.1361	Loss: 0.2982	
Train:	Epoch:[59][8/11]   	Acc: 1.000	Label_Loss: 0.0483	Top_Loss: 0.0928	Bottom_Loss: 0.1054	Loss: 0.2465	
Subject: 006, n=11 | test_f1: 0.42105 | val_f1: 0.53871 |best_f1: 0.64708
Train:	Epoch:[60][1/11]   	Acc: 1.000	Label_Loss: 0.0682	Top_Loss: 0.1848	Bottom_Loss: 0.1133	Loss: 0.3663	
Train:	Epoch:[60][8/11]   	Acc: 0.969	Label_Loss: 0.1415	Top_Loss: 0.1619	Bottom_Loss: 0.2714	Loss: 0.5748	
Subject: 006, n=11 | test

Train:	Epoch:[86][1/11]   	Acc: 1.000	Label_Loss: 0.0154	Top_Loss: 0.0803	Bottom_Loss: 0.0634	Loss: 0.1591	
Train:	Epoch:[86][8/11]   	Acc: 1.000	Label_Loss: 0.0203	Top_Loss: 0.0398	Bottom_Loss: 0.0796	Loss: 0.1397	
Subject: 006, n=11 | test_f1: 0.42105 | val_f1: 0.5522 |best_f1: 0.64708
Train:	Epoch:[87][1/11]   	Acc: 1.000	Label_Loss: 0.0106	Top_Loss: 0.0247	Bottom_Loss: 0.0349	Loss: 0.0702	
Train:	Epoch:[87][8/11]   	Acc: 1.000	Label_Loss: 0.0379	Top_Loss: 0.0751	Bottom_Loss: 0.0966	Loss: 0.2096	
Subject: 006, n=11 | test_f1: 0.42105 | val_f1: 0.46473 |best_f1: 0.64708
Train:	Epoch:[88][1/11]   	Acc: 1.000	Label_Loss: 0.0230	Top_Loss: 0.0551	Bottom_Loss: 0.0839	Loss: 0.1620	
Train:	Epoch:[88][8/11]   	Acc: 1.000	Label_Loss: 0.0121	Top_Loss: 0.0462	Bottom_Loss: 0.0279	Loss: 0.0862	
Subject: 006, n=11 | test_f1: 0.45 | val_f1: 0.554 |best_f1: 0.64708
Train:	Epoch:[89][1/11]   	Acc: 1.000	Label_Loss: 0.0059	Top_Loss: 0.0198	Bottom_Loss: 0.0347	Loss: 0.0604	
Train:	Epoch:[89][8/11]   	A

Subject: 007, n=08 | test_f1: 0.074074 | val_f1: 0.49439 |best_f1: 0.50151
Train:	Epoch:[15][1/11]   	Acc: 0.875	Label_Loss: 0.5110	Top_Loss: 0.6513	Bottom_Loss: 0.6917	Loss: 1.8540	
Train:	Epoch:[15][8/11]   	Acc: 0.812	Label_Loss: 0.3822	Top_Loss: 0.5391	Bottom_Loss: 0.5599	Loss: 1.4813	
Subject: 007, n=08 | test_f1: 0.074074 | val_f1: 0.42741 |best_f1: 0.50151
Train:	Epoch:[16][1/11]   	Acc: 0.844	Label_Loss: 0.3129	Top_Loss: 0.4058	Bottom_Loss: 0.5244	Loss: 1.2431	
Train:	Epoch:[16][8/11]   	Acc: 0.594	Label_Loss: 0.6624	Top_Loss: 0.5987	Bottom_Loss: 0.6343	Loss: 1.8955	
Subject: 007, n=08 | test_f1: 0.074074 | val_f1: 0.51564 |best_f1: 0.51564
Train:	Epoch:[17][1/11]   	Acc: 0.844	Label_Loss: 0.4896	Top_Loss: 0.7665	Bottom_Loss: 0.6523	Loss: 1.9084	
Train:	Epoch:[17][8/11]   	Acc: 0.812	Label_Loss: 0.5563	Top_Loss: 0.6804	Bottom_Loss: 0.7336	Loss: 1.9703	
Subject: 007, n=08 | test_f1: 0.074074 | val_f1: 0.41265 |best_f1: 0.51564
Train:	Epoch:[18][1/11]   	Acc: 0.906	Label_Loss: 0.

...

Train:	Epoch:[58][1/11]   	Acc: 1.000	Label_Loss: 0.1082	Top_Loss: 0.1995	Bottom_Loss: 0.1520	Loss: 0.4598	
Train:	Epoch:[58][8/11]   	Acc: 1.000	Label_Loss: 0.0748	Top_Loss: 0.0851	Bottom_Loss: 0.1292	Loss: 0.2891	
Subject: s8, n=13 | test_f1: 0.39259 | val_f1: 0.63204 |best_f1: 0.63878
Train:	Epoch:[59][1/11]   	Acc: 1.000	Label_Loss: 0.0554	Top_Loss: 0.0851	Bottom_Loss: 0.2567	Loss: 0.3971	
Train:	Epoch:[59][8/11]   	Acc: 1.000	Label_Loss: 0.0543	Top_Loss: 0.1081	Bottom_Loss: 0.1127	Loss: 0.2752	
Subject: s8, n=13 | test_f1: 0.24908 | val_f1: 0.58859 |best_f1: 0.63878
Train:	Epoch:[60][1/11]   	Acc: 1.000	Label_Loss: 0.0909	Top_Loss: 0.0969	Bottom_Loss: 0.1526	Loss: 0.3405	
Train:	Epoch:[60][8/11]   	Acc: 1.000	Label_Loss: 0.0524	Top_Loss: 0.0876	Bottom_Loss: 0.1073	Loss: 0.2474	
Subject: s8, n=13 | test_f1: 0.36111 | val_f1: 0.55927 |best_f1: 0.63878
Train:	Epoch:[61][1/11]   	Acc: 1.000	Label_Loss: 0.0822	Top_Loss: 0.1474	Bottom_Loss: 0.2001	Loss: 0.4297	
Train:	Epoch:[61][8/11]  

Subject: s8, n=13 | test_f1: 0.47179 | val_f1: 0.54185 |best_f1: 0.64833
Train:	Epoch:[87][1/11]   	Acc: 1.000	Label_Loss: 0.0092	Top_Loss: 0.0206	Bottom_Loss: 0.0357	Loss: 0.0655	
Train:	Epoch:[87][8/11]   	Acc: 1.000	Label_Loss: 0.0149	Top_Loss: 0.0311	Bottom_Loss: 0.0311	Loss: 0.0772	
Subject: s8, n=13 | test_f1: 0.38624 | val_f1: 0.65266 |best_f1: 0.65266
Train:	Epoch:[88][1/11]   	Acc: 1.000	Label_Loss: 0.0546	Top_Loss: 0.0680	Bottom_Loss: 0.0747	Loss: 0.1973	
Train:	Epoch:[88][8/11]   	Acc: 1.000	Label_Loss: 0.0081	Top_Loss: 0.0315	Bottom_Loss: 0.0370	Loss: 0.0766	
Subject: s8, n=13 | test_f1: 0.4381 | val_f1: 0.6366 |best_f1: 0.65266
Train:	Epoch:[89][1/11]   	Acc: 1.000	Label_Loss: 0.0119	Top_Loss: 0.0351	Bottom_Loss: 0.0258	Loss: 0.0727	
Train:	Epoch:[89][8/11]   	Acc: 1.000	Label_Loss: 0.0063	Top_Loss: 0.0173	Bottom_Loss: 0.0253	Loss: 0.0489	
Subject: s8, n=13 | test_f1: 0.38889 | val_f1: 0.60089 |best_f1: 0.65266
Train:	Epoch:[90][1/11]   	Acc: 1.000	Label_Loss: 0.0215	Top_L

Train:	Epoch:[15][8/11]   	Acc: 0.844	Label_Loss: 0.4182	Top_Loss: 0.5916	Bottom_Loss: 0.6492	Loss: 1.6590	
Subject: s9, n=04 | test_f1: 0.2 | val_f1: 0.46055 |best_f1: 0.59033
Train:	Epoch:[16][1/11]   	Acc: 0.812	Label_Loss: 0.4820	Top_Loss: 0.5027	Bottom_Loss: 0.6587	Loss: 1.6433	
Train:	Epoch:[16][8/11]   	Acc: 0.719	Label_Loss: 0.5976	Top_Loss: 0.7015	Bottom_Loss: 0.7498	Loss: 2.0489	
Subject: s9, n=04 | test_f1: 0.16667 | val_f1: 0.47385 |best_f1: 0.59033
Train:	Epoch:[17][1/11]   	Acc: 0.719	Label_Loss: 0.5669	Top_Loss: 0.5931	Bottom_Loss: 0.5993	Loss: 1.7594	
Train:	Epoch:[17][8/11]   	Acc: 0.719	Label_Loss: 0.5912	Top_Loss: 0.6415	Bottom_Loss: 0.6426	Loss: 1.8753	
Subject: s9, n=04 | test_f1: 0.0 | val_f1: 0.49107 |best_f1: 0.59033
Train:	Epoch:[18][1/11]   	Acc: 0.781	Label_Loss: 0.4908	Top_Loss: 0.6517	Bottom_Loss: 0.5898	Loss: 1.7324	
Train:	Epoch:[18][8/11]   	Acc: 0.812	Label_Loss: 0.5002	Top_Loss: 0.5259	Bottom_Loss: 0.6466	Loss: 1.6726	
Subject: s9, n=04 | test_f1: 0.22

Train:	Epoch:[44][1/11]   	Acc: 0.969	Label_Loss: 0.1432	Top_Loss: 0.2444	Bottom_Loss: 0.2264	Loss: 0.6141	
Train:	Epoch:[44][8/11]   	Acc: 0.938	Label_Loss: 0.1556	Top_Loss: 0.3531	Bottom_Loss: 0.1903	Loss: 0.6989	
Subject: s9, n=04 | test_f1: 0.26667 | val_f1: 0.5218 |best_f1: 0.6063
Train:	Epoch:[45][1/11]   	Acc: 0.875	Label_Loss: 0.2386	Top_Loss: 0.2436	Bottom_Loss: 0.2072	Loss: 0.6895	
Train:	Epoch:[45][8/11]   	Acc: 0.938	Label_Loss: 0.1473	Top_Loss: 0.2903	Bottom_Loss: 0.2444	Loss: 0.6820	
Subject: s9, n=04 | test_f1: 0.22222 | val_f1: 0.50609 |best_f1: 0.6063
Train:	Epoch:[46][1/11]   	Acc: 1.000	Label_Loss: 0.0844	Top_Loss: 0.1617	Bottom_Loss: 0.2893	Loss: 0.5354	
Train:	Epoch:[46][8/11]   	Acc: 0.938	Label_Loss: 0.2798	Top_Loss: 0.5872	Bottom_Loss: 0.2318	Loss: 1.0988	
Subject: s9, n=04 | test_f1: 0.38889 | val_f1: 0.54958 |best_f1: 0.6063
Train:	Epoch:[47][1/11]   	Acc: 1.000	Label_Loss: 0.0901	Top_Loss: 0.1961	Bottom_Loss: 0.1592	Loss: 0.4454	
Train:	Epoch:[47][8/11]   	Ac

Subject: s9, n=04 | test_f1: 0.6 | val_f1: 0.49578 |best_f1: 0.6063
Train:	Epoch:[73][1/11]   	Acc: 0.969	Label_Loss: 0.0586	Top_Loss: 0.1602	Bottom_Loss: 0.1057	Loss: 0.3245	
Train:	Epoch:[73][8/11]   	Acc: 1.000	Label_Loss: 0.0332	Top_Loss: 0.0977	Bottom_Loss: 0.0883	Loss: 0.2192	
Subject: s9, n=04 | test_f1: 0.16667 | val_f1: 0.56252 |best_f1: 0.6063
Train:	Epoch:[74][1/11]   	Acc: 1.000	Label_Loss: 0.0310	Top_Loss: 0.1465	Bottom_Loss: 0.0934	Loss: 0.2710	
Train:	Epoch:[74][8/11]   	Acc: 1.000	Label_Loss: 0.0242	Top_Loss: 0.1433	Bottom_Loss: 0.0777	Loss: 0.2452	
Subject: s9, n=04 | test_f1: 0.33333 | val_f1: 0.51111 |best_f1: 0.6063
Train:	Epoch:[75][1/11]   	Acc: 1.000	Label_Loss: 0.0264	Top_Loss: 0.1253	Bottom_Loss: 0.0865	Loss: 0.2382	
Train:	Epoch:[75][8/11]   	Acc: 1.000	Label_Loss: 0.0425	Top_Loss: 0.1229	Bottom_Loss: 0.0419	Loss: 0.2073	
Subject: s9, n=04 | test_f1: 0.0 | val_f1: 0.6011 |best_f1: 0.6063
Train:	Epoch:[76][1/11]   	Acc: 0.938	Label_Loss: 0.0878	Top_Loss: 0.1082

In [18]:
def train(train_dataloader, model, criterion, optimizer, epoch, print_freq=7):

    model['resnet'].train()
    model['fc_top'].train()
    model['fc_bottom'].train()
    model['classifier'].train()
    model['classifier_top'].train()
    model['classifier_bottom'].train()

    correct = 0

    for i, sample in enumerate(train_dataloader):
        input, label = sample['image'].to(device), sample['label'].to(device)

        output_resnet_top, output_resnet_bottom = model['resnet'](input)

        output_fc_top = model['fc_top'](output_resnet_top)
        output_fc_bottom = model['fc_bottom'](output_resnet_bottom)

        features = torch.cat((output_fc_top, output_fc_bottom), 1)

        output = model['classifier'](features)
        output_top = model['classifier_top'](output_fc_top)
        output_bottom = model['classifier_bottom'](output_fc_bottom)

        loss_label = criterion(output, label)
        loss_top = criterion(output_top, label)
        loss_bottom = criterion(output_bottom, label)

        loss = loss_label + loss_top + loss_bottom

        _, preds = torch.max(output, dim=1)

        correct = float((label.int() == preds.int()).sum())
        accuracy = correct / len(label)

        optimizer.zero_grad()
        loss.backward()
        
        Clip_Norm = 1
        nn.utils.clip_grad_norm_(
            model['resnet'].parameters(), Clip_Norm, norm_type=2)
        nn.utils.clip_grad_norm_(
            model['fc_top'].parameters(), Clip_Norm, norm_type=2)
        nn.utils.clip_grad_norm_(
            model['fc_bottom'].parameters(), Clip_Norm, norm_type=2)
        nn.utils.clip_grad_norm_(
            model['classifier'].parameters(), Clip_Norm, norm_type=2)
        nn.utils.clip_grad_norm_(
            model['classifier_top'].parameters(), Clip_Norm, norm_type=2)
        nn.utils.clip_grad_norm_(
            model['classifier_bottom'].parameters(), Clip_Norm, norm_type=2)

        optimizer.step()

        if i % print_freq == 0:
            print('Train:\t'
                  'Epoch:[{0}][{1}/{2}]   \t'
                  'Acc: {acc:.3f}\t'
                  'Label_Loss: {l_loss:.4f}\t'
                  'Top_Loss: {t_loss:.4f}\t'
                  'Bottom_Loss: {b_loss:.4f}\t'
                  'Loss: {loss:.4f}\t'.format(
                      epoch, i + 1, len(train_dataloader), acc=accuracy,
                      l_loss=loss_label, t_loss=loss_top, b_loss=loss_bottom, loss=loss))
            
            
def validate(validate_dataloader, model, criterion, epoch):

    model['resnet'].eval()
    model['fc_top'].eval()
    model['fc_bottom'].eval()
    model['classifier'].eval()
    model['classifier_top'].eval()
    model['classifier_bottom'].eval()

    losses = 0
    correctes = 0
    preds_return = torch.LongTensor([])
    target_return = torch.LongTensor([])

    sample_file = {}

    with torch.no_grad():
        for sample in validate_dataloader:
            input, target = sample['image'].to(device), sample['label'].to(device)

            output_resnet_top, output_resnet_bottom = model['resnet'](input)
            output_fc_top = model['fc_top'](output_resnet_top)
            output_fc_bottom = model['fc_bottom'](output_resnet_bottom)

            output_model = torch.cat((output_fc_top, output_fc_bottom), 1)

            output = model['classifier'](output_model)

            loss = criterion(output, target)

            _, preds = torch.max(output, dim=1)

            preds_return = torch.cat((preds_return, preds.cpu()), 0)
            target_return = torch.cat((target_return, target.cpu()), 0)

            losses += loss

    return preds_return, target_return, losses


In [52]:
# With test data
def LOSO(features, df, epochs=200, lr=0.01, batch_size=128, dropout=0.5, weight_decay=0.001, early_stopping=False,
         verbose=True):
    outputs_list = []
    #groupby reorders elements, now the labels are in same order as outputs
    df_groupby = pd.concat([i[1] for i in df.groupby("subject")])
    dataset_groupby = df_groupby["dataset"]
    
    le = LabelEncoder()
    labels = le.fit_transform(df["emotion"])
    labels_groupby = le.transform(df_groupby["emotion"])

    #loop over each subject
    for group in df.groupby("subject"):
        subject = group[0]
        #split data to train and test based on the subject index
        train_index = df[df["subject"] != subject].index
        X_train = features[train_index, :]
        y_train = labels[train_index]
        
        test_index = df[df["subject"] == subject].index
        X_test = features[test_index, :]
        y_test = labels[test_index]

        #create pytorch dataloaders from the split
        megc_dataset_train = MEData(X_train, y_train, transform)
        train_loader = torch.utils.data.DataLoader(megc_dataset_train,
                                                             batch_size=batch_size, shuffle=True,
                                                             num_workers=0)

        megc_dataset_test = MEData(X_test, y_test, transform)
        test_loader = torch.utils.data.DataLoader(megc_dataset_test,
                                                         batch_size=100, shuffle=False,
                                                         num_workers=0)

        
        model = Flow_Part_npic()
        model['resnet'] = model['resnet'].to(device)
        model['fc_top'] = model['fc_top'].to(device)
        model['fc_bottom'] = model['fc_bottom'].to(device)
        model['fc_top'] = model['fc_top'].apply(weight_init)
        model['fc_bottom'] = model['fc_bottom'].apply(weight_init)

        model['classifier'] = model['classifier'].to(device)
        model['classifier_top'] = model['classifier_top'].to(device)
        model['classifier_bottom'] = model['classifier_bottom'].to(device)

        model['classifier'] = model['classifier'].apply(weight_init)
        model['classifier_top'] = model['classifier_top'].apply(weight_init)
        model['classifier_bottom'] = model['classifier_bottom'].apply(
            weight_init)
        
        criterion = nn.CrossEntropyLoss()
        optimizer = optim.Adam([
            {'params': model['resnet'].parameters(), 'lr':0.00001},
            {'params': model['fc_top'].parameters(), 'lr':LEARNING_RATE},
            {'params': model['fc_bottom'].parameters(), 'lr':LEARNING_RATE},
            {'params': model['classifier'].parameters(), 'lr':LEARNING_RATE},
            {'params': model['classifier_top'].parameters(),
             'lr':LEARNING_RATE},
            {'params': model['classifier_bottom'].parameters(),
             'lr':LEARNING_RATE},
        ], weight_decay=weight_decay)
        
        
        Epoch_F1_score = 0
        for epoch in range(epochs):
            if epoch % 10 == 0 and epoch != 0:
                if optimizer.param_groups[2]['lr'] > 0.00001:
                    optimizer.param_groups[1]['lr'] = optimizer.param_groups[1]['lr'] * 0.5
                    optimizer.param_groups[2]['lr'] = optimizer.param_groups[2]['lr'] * 0.5
                    optimizer.param_groups[3]['lr'] = optimizer.param_groups[3]['lr'] * 0.5
                    optimizer.param_groups[4]['lr'] = optimizer.param_groups[4]['lr'] * 0.5
                    optimizer.param_groups[5]['lr'] = optimizer.param_groups[5]['lr'] * 0.5
                    
            train(train_loader, model, criterion, optimizer, epoch)
            preds, target, loss = validate(test_loader, model, criterion, epoch)
            
            preds = preds.cpu().detach().data.numpy()
            test_f1 = f1_score(preds, target.cpu().data.numpy(), average="macro")
            
            if test_f1 >= Epoch_F1_score:
                Epoch_F1_score = test_f1
                best_preds = preds
            #Print statistics
            if verbose:
                print("Subject: {}, n={} | test_f1: {:.5} |best_f1: {:.5}".format(
                    subject, str(target.shape[0]).zfill(2), test_f1, Epoch_F1_score))
        if early_stopping:
            outputs_list.append(best_preds)
        else:
            outputs_list.append(preds)
            
    outputs = np.concatenate(outputs_list)
    f1_total = f1_score(labels_groupby, outputs, average="macro")
    idx = dataset_groupby == "smic"
    f1_smic = f1_score(labels_groupby[idx], outputs[idx], average="macro")
    idx = dataset_groupby == "casme2"
    f1_casme2 = f1_score(labels_groupby[idx], outputs[idx], average="macro")
    idx = dataset_groupby == "samm"
    f1_samm = f1_score(labels_groupby[idx], outputs[idx], average="macro")
    print("Total f1: {}, SMIC: {}, CASME2: {}, SAMM: {}".format(f1_total, f1_smic, f1_casme2, f1_samm))

In [19]:
from sklearn.model_selection import train_test_split

In [20]:
#With validation data
def LOSO(features, df, epochs=200, lr=0.01, batch_size=128, dropout=0.5, weight_decay=0.001, early_stopping=False,
         verbose=True):
    outputs_list = []
    #groupby reorders elements, now the labels are in same order as outputs
    df_groupby = pd.concat([i[1] for i in df.groupby("subject")])
    dataset_groupby = df_groupby["dataset"]
    
    le = LabelEncoder()
    labels = le.fit_transform(df["emotion"])
    labels_groupby = le.transform(df_groupby["emotion"])

    #loop over each subject
    for group in df.groupby("subject"):
        subject = group[0]
        #split data to train and test based on the subject index
        nons_index = df[df["subject"] != subject].index
        X_nons = features[nons_index, :]
        y_nons = labels[nons_index]
        
        #Split non-subject data to train and validation data
        X_train, X_val, y_train, y_val = train_test_split(X_nons, y_nons, test_size=0.2, random_state=0)
        
        test_index = df[df["subject"] == subject].index
        X_test = features[test_index, :]
        y_test = labels[test_index]

        #create pytorch dataloaders from the split
        megc_dataset_train = MEData(X_train, y_train, transform)
        train_loader = torch.utils.data.DataLoader(megc_dataset_train,
                                                             batch_size=batch_size, shuffle=True,
                                                             num_workers=0)
        
        megc_dataset_val = MEData(X_val, y_val, transform)
        val_loader = torch.utils.data.DataLoader(megc_dataset_val,
                                                             batch_size=batch_size, shuffle=False,
                                                             num_workers=0)

        megc_dataset_test = MEData(X_test, y_test, transform)
        test_loader = torch.utils.data.DataLoader(megc_dataset_test,
                                                         batch_size=100, shuffle=False,
                                                         num_workers=0)

        
        model = Flow_Part_npic()
        model['resnet'] = model['resnet'].to(device)
        model['fc_top'] = model['fc_top'].to(device)
        model['fc_bottom'] = model['fc_bottom'].to(device)
        model['fc_top'] = model['fc_top'].apply(weight_init)
        model['fc_bottom'] = model['fc_bottom'].apply(weight_init)

        model['classifier'] = model['classifier'].to(device)
        model['classifier_top'] = model['classifier_top'].to(device)
        model['classifier_bottom'] = model['classifier_bottom'].to(device)

        model['classifier'] = model['classifier'].apply(weight_init)
        model['classifier_top'] = model['classifier_top'].apply(weight_init)
        model['classifier_bottom'] = model['classifier_bottom'].apply(
            weight_init)
        
        criterion = nn.CrossEntropyLoss()
        optimizer = optim.Adam([
            {'params': model['resnet'].parameters(), 'lr':0.00001},
            {'params': model['fc_top'].parameters(), 'lr':LEARNING_RATE},
            {'params': model['fc_bottom'].parameters(), 'lr':LEARNING_RATE},
            {'params': model['classifier'].parameters(), 'lr':LEARNING_RATE},
            {'params': model['classifier_top'].parameters(),
             'lr':LEARNING_RATE},
            {'params': model['classifier_bottom'].parameters(),
             'lr':LEARNING_RATE},
        ], weight_decay=weight_decay)
        
        
        Epoch_F1_score = 0
        for epoch in range(epochs):
            if epoch % 10 == 0 and epoch != 0:
                if optimizer.param_groups[2]['lr'] > 0.00001:
                    optimizer.param_groups[1]['lr'] = optimizer.param_groups[1]['lr'] * 0.5
                    optimizer.param_groups[2]['lr'] = optimizer.param_groups[2]['lr'] * 0.5
                    optimizer.param_groups[3]['lr'] = optimizer.param_groups[3]['lr'] * 0.5
                    optimizer.param_groups[4]['lr'] = optimizer.param_groups[4]['lr'] * 0.5
                    optimizer.param_groups[5]['lr'] = optimizer.param_groups[5]['lr'] * 0.5
                    
            train(train_loader, model, criterion, optimizer, epoch)
            val_preds, val_target, val_loss = validate(val_loader, model, criterion, epoch)
            preds, target, loss = validate(test_loader, model, criterion, epoch)
            
            val_preds = val_preds.cpu().detach().data.numpy()
            val_f1 = f1_score(val_preds, val_target.cpu().data.numpy(), average="macro")
            
            preds = preds.cpu().detach().data.numpy()
            test_f1 = f1_score(preds, target.cpu().data.numpy(), average="macro")
            
            if val_f1 >= Epoch_F1_score:
                Epoch_F1_score = val_f1
                best_preds = preds
            #Print statistics
            if verbose:
                print("Subject: {}, n={} | test_f1: {:.5} | val_f1: {:.5} |best_f1: {:.5}".format(
                    subject, str(target.shape[0]).zfill(2), test_f1, val_f1, Epoch_F1_score))
        if early_stopping:
            outputs_list.append(best_preds)
        else:
            outputs_list.append(preds)
            
    outputs = np.concatenate(outputs_list)
    f1_total = f1_score(labels_groupby, outputs, average="macro")
    idx = dataset_groupby == "smic"
    f1_smic = f1_score(labels_groupby[idx], outputs[idx], average="macro")
    idx = dataset_groupby == "casme2"
    f1_casme2 = f1_score(labels_groupby[idx], outputs[idx], average="macro")
    idx = dataset_groupby == "samm"
    f1_samm = f1_score(labels_groupby[idx], outputs[idx], average="macro")
    print("Total f1: {}, SMIC: {}, CASME2: {}, SAMM: {}".format(f1_total, f1_smic, f1_casme2, f1_samm))